In [0]:
#@title Set up logic

class Regulation:

  def c(self):
    return 0.10

  def p_c_max(self):
    return 700
  
  def d_min(self):
    return 300

  def d_max(self):
    return 2500


class InsuranceProvider:

  def __init__(self, monthly_premium):
    self.monthly_premium = monthly_premium

  def issue_policy(self, deductible):
    return InsurancePolicy(
        deductible=deductible,
        monthly_premium=self.monthly_premium[deductible])

  def deductibles(self):
    return sorted(self.monthly_premium.keys())

  def monthly_premiums(self):
    return [self.monthly_premium[d] for d in self.deductibles()]


class InsurancePolicy:

  def __init__(self, deductible, monthly_premium):
    self.deductible = deductible
    self.monthly_premium = monthly_premium
    self.regulation = Regulation()
    assert(deductible >= self.regulation.d_min())
    assert(deductible <= self.regulation.d_max())
    assert(monthly_premium >= 0)

  def d(self):
    return self.deductible

  def m(self):
    return self.monthly_premium 

  def c(self):
    return self.regulation.c()
  
  def p_c_max(self):
    return self.regulation.p_c_max()


class Scenario:

  def __init__(self,
               policy,
               healthcare_services):
    assert(healthcare_services >= 0)
    self.policy = policy
    self.healthcare_services = healthcare_services

  def m(self):
    return self.policy.m()

  def d(self):
    return self.policy.d()

  def h(self):
    return self.healthcare_services

  def p(self):
    return self.p_d() + self.p_c()

  def p_c(self):
    return min(
        self.policy.c() * max(self.h() - self.d(), 0),
        self.policy.p_c_max())

  def p_d(self):
    return min(self.d(), self.h())

  def i(self):
    return self.h() - self.p()

  def e(self):
    return 12 * self.m() + self.p()


In [0]:
#@title Create sample insurance provider

insurer = InsuranceProvider({
            300: 418,
            500: 407,
            1000: 379,
            1500: 352,
            2000: 325,
            2500: 298,
          })


In [0]:
#@title Set up plotting

from matplotlib import pyplot as plt
import seaborn

_width = 700.0 / (936.0 / 13.0)
_output_count = 1

def savefigure():
  global _output_count
  plt.savefig('output%02d' % _output_count)
  _output_count = _output_count + 1

hs = range(0, 10000, 10)

In [0]:
#@title Consumed health services vs. policyholder contribution

_, ax = plt.subplots(figsize=(_width, 5))
d = min(insurer.deductibles())
ps = [Scenario(policy=insurer.issue_policy(deductible=d),
                healthcare_services=h).p()
      for h in hs]
ax.set_title('Consumed health services vs. policyholder contribution')
ax.set_xlabel('consumed health services [CHF]')
ax.set_ylabel('policyholder contributions [CHF]')
seaborn.lineplot(hs, ps, label='%d CHF deductible' % d);
savefigure()

_, ax = plt.subplots(figsize=(_width, 5))
ax.set_title('Consumed health services vs. policyholder contribution')
ax.set_xlabel('consumed health services [CHF]')
ax.set_ylabel('policyholder contributions [CHF]')
for d in insurer.deductibles():
  ps = [Scenario(policy=insurer.issue_policy(deductible=d),
                 healthcare_services=h).p()
        for h in hs]
  seaborn.lineplot(hs, ps, label='%d CHF deductible' % d)
savefigure()


In [0]:
#@title Consumed health services vs. net expense

_, ax = plt.subplots(figsize=(_width, 5))
d = min(insurer.deductibles())
es = [Scenario(policy=insurer.issue_policy(deductible=d),
                healthcare_services=h).e()
      for h in hs]
ax.set_title('Consumed health services vs. net expense')
ax.set_xlabel('consumed health services [CHF]')
ax.set_ylabel('net expense [CHF]')
seaborn.lineplot(hs,
                 es,
                 label='%d CHF deductible' % d);
savefigure()

_, ax = plt.subplots(figsize=(_width, 5))
ax.set_title('Consumed health services vs. net expense')
ax.set_xlabel('consumed health services [CHF]')
ax.set_ylabel('net expense [CHF]')
for d in insurer.deductibles():
  es = [Scenario(policy=insurer.issue_policy(deductible=d),
                 healthcare_services=h).e()
        for h in hs]
  seaborn.lineplot(hs, es, label='%d CHF deductible' % d)
savefigure()


In [0]:
#@title Impact of deductible on net expenses

res = []
for h in hs:
  es = [Scenario(policy=insurer.issue_policy(deductible=d),
                 healthcare_services=h).e()
        for d in insurer.deductibles()]
  res.append(max(es) - min(es))


_, ax = plt.subplots(figsize=(_width, 5))
ax.set_title('Impact of deductible on net expenses')
ax.set_xlabel('consumed health services [CHF]')
ax.set_ylabel('impact [CHF]')
seaborn.lineplot(hs, res)
savefigure()


In [0]:
#@title Deductible s. monthly premium

_, ax = plt.subplots(figsize=(_width, 5))
ax.set_title('Deductible vs. monthly premium')
ax.set_xlabel('deductible [CHF]')
ax.set_ylabel('monthly premium [CHF]')
seaborn.pointplot(insurer.deductibles(),
                  insurer.monthly_premiums(),
                  linestyles='--')
savefigure()